![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Komputerowe wspomaganie tłumaczenia </h1>
<h2> 9,10. <i>Web scraping</i> [laboratoria]</h2> 
<h3>Rafał Jaworski (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

Jak dobrze wiemy, w procesie wspomagania tłumaczenia oraz w zagadnieniach przetwarzania języka naturalnego ogromną rolę pełnią zasoby lingwistyczne. Należą do nich korpusy równoległe (pamięci tłumaczeń), korpusy jednojęzyczne oraz słowniki. Bywa, że zasoby te nie są dostępne dla języka, nad którym chcemy pracować.

W tej sytuacji jest jeszcze dla nas ratunek - możemy skorzystać z zasobów dostępnych publicznie w Internecie. Na dzisiejszych zajęciach przećwiczymy techniki pobierania tekstu ze stron internetowych.

Poniższy kod służy do ściągnięcia zawartości strony (w formacie HTML do zmiennej) oraz do wyszukania na tej stronie konkretnych elementów. Przed jego uruchomieniem należy zainstalować moduł BeautifulSoup:
`pip3 install beautifulsoup4`

In [19]:
import warnings
warnings.filterwarnings('ignore')

In [20]:
import requests
from bs4 import BeautifulSoup

url='https://epoznan.pl'

page = requests.get(url)
soup = BeautifulSoup(page.content, 'html.parser')

headers = soup.find_all('h3', {'class':'postItem__title'})

print('\n'.join([header.get_text() for header in headers]))

Wypadek na Dąbrowskiego. Jedno z aut dachowało
Znów gęsty dym nad miastem
IMGW ostrzega. W 19 powiatach naszego regionu!
Kolejna inwestycja zakończona. Na samym Starym Rynku
Lech przegrał z Legią w Poznaniu. Dwa gole samobójcze
W każdym elektrycznym Volkswagenie ID znajdziemy "kawałek Poznania"
Takie parkomaty stawiają na poznańskich ulicach. Będzie dużo nowości. Za parkowanie zapłacimy kartą i blikiem
Policjanci publikują wizerunek i szukają jednego z klientów poznańskiego pubu
Zielone naklejki na lampach w poznańskich parkach. Co oznaczają?
Nowy sposób oszustów. Mogą pisać takie wiadomości
Szukamy Ciebie! Najlepsze oferty pracy dla osób z niepełnosprawnościami
Park przemysłowy pod Poznaniem sprzedany za 92,5 mln euro
Warta zagrała w Krakowie
"Biały dym" nad miastem. Po przejeździe pociągu z kibicami Legii Warszawa?
Czytelnik zwraca uwagę na kolejne niebezpieczne skrzyżowanie w Poznaniu. "W tym miejscu nie ma znaku"
Jeżdżą i robią ważne badania w Wielkopolsce. W maju zaplanowanych jes

### Ćwiczenie 1: Napisz funkcję do pobierania nazw towarów z serwisu Ceneo.pl. Typ towaru, np. telewizor, pralka, laptop jest parametrem funkcji. Wystarczy pobierać dane z pierwszej strony wyników wyszukiwania.

In [21]:
def get_names(article_type):
    url = f"https://m.ceneo.pl/;szukaj-{article_type}"

    page = requests.get(url)
    soup = BeautifulSoup(page.content, 'html.parser')

    prod_names = soup.find_all('div', {'class':'list-prod-name'})
    prod_names = [prod_name.get_text().strip() for prod_name in prod_names]

    return prod_names

In [22]:
get_names('telewizor')[-3:]

['Telewizor LED TCL 43P638 43 cale 4K UHD',
 'Telewizor LED LG 32LQ630B6LA 32 cale HD Ready',
 'Telewizor LED Xiaomi Mi LED TV P1 43 cale 4K UHD']

In [23]:
get_names('pralka')[-3:]

['Pralka Electrolux PerfectCare 600 EW6SM404WP',
 'Pralka MPM MPM-4610-PH-03',
 'Pralka Whirlpool FFS 7259 B EE']

In [24]:
get_names('laptop')[-3:]

['Laptop Acer Nitro 16 AN16-41 R7-7840HS/16GB/1TB/RTX4070/W11 165Hz',
 'Laptop Lenovo IdeaPad Slim 3 15ABR8 15,6"/Ryzen5/16GB/512GB/NoOS (82XM009NPB)',
 'Laptop Dell Latitude 7640 16"/i7/32GB/1TB/Win11 (N010L764016EMEA_VP)']

W ten sposób pobieramy dane z jednej strony. Nic jednak nie stoi nam na przeszkodzie, aby zasymulować przełączanie stron.

### Ćwiczenie 2: Zaobserwuj, jak zmienia się url strony podczas przechodzenia do kolejnych stron wyników wyszukiwania na Ceneo.pl. Wykorzystaj tę informację i uruchom funkcję get_names() na więcej niż jednej stronie wyników.

In [25]:
def scrape_names(article_type: str, num_pages: int):
    url = f"https://m.ceneo.pl/;szukaj-{article_type}"
    page = requests.get(url)

    prod_names = []
    for page_idx in range(1, num_pages+1):
        tmp_page = requests.get(f"{page.url};0020-30-0-0-{page_idx}.htm")
        soup = BeautifulSoup(tmp_page.content, 'html.parser')

        tmp_prod_names = soup.find_all('div', {'class':'list-prod-name'})
        tmp_prod_names = [prod_name.find('span') for prod_name in tmp_prod_names]
        tmp_prod_names = [prod_name.get_text().strip() for prod_name in tmp_prod_names]

        prod_names.extend(tmp_prod_names)

    return prod_names

In [26]:
scrape_names('telewizor', 3)[-3:]

['Telewizor LED LG 70UR80003LJ 70 cali 4K UHD',
 'Telewizor QLED Samsung QE85Q70C 85 cali 4K UHD',
 'Telewizor LED Hisense 32A4K 32 cale 4K UHD']

In [27]:
scrape_names('pralka', 3)[-3:]

['Pralka Bosch Serie 4 WGG0440EPL',
 'Pralka Haier I-Pro 3 HW90-BP14939',
 'Pralka Samsung WW11BGA046AE']

In [28]:
scrape_names('laptop', 3)[-3:]

['Laptop Dell Latitude 3340 13,3"/i3/8GB/256GB/Win11 (L1333400023853SA)',
 'Laptop HP ZBook Firefly 14 G8 14"/i7/16GB/512GB/Win10 (2C9R0EA)',
 'Laptop HP 17-CN3053 17,3"/i5/32GB/2TB/Win11 (7F8G5UA)']

Technika pobierania treści z Internetu jest szczególnie efektywnym sposobem na pozyskiwanie dużych ilości tekstu. Poniższy fragment kodu służy do ściągnięcia całości tekstu ze strony.

In [29]:
import re

url = "https://www.yahoo.com"

page = requests.get(url)
soup = BeautifulSoup(page.content, 'html.parser')

# usunięcie elementów script i style
for script in soup(["script", "style"]):
    script.extract()    # usuń element

# pobierz tekst
text = soup.get_text()

# usuń wielokrotne białe znaki
text = re.sub(r"\s+", " ", text)

print(text)

Yahoo | Mail, Weather, Search, Politics, News, Finance, Sports & Videos News Today's news US Politics World Tech Reviews and deals Audio Computing Gaming Health Home Phones Science TVs Climate change Health Science 2024 election Originals The 360 Life Health COVID-19 Fall allergies Health news Mental health Relax Sexual health Studies The Unwind Parenting Family health So mini ways Style and beauty It Figures Unapologetically Horoscopes Shopping Buying guides Food Travel Autos Gift ideas Buying guides Entertainment Celebrity TV Movies Music How to Watch Interviews Videos Shopping Finance My portfolio My watchlist News Stock market Economics Earnings Crypto Politics Biden economy Personal finance Markets Stocks: most active Stocks: gainers Stocks: losers Trending tickers Futures World indices US Treasury bonds Currencies Crypto Top ETFs Top mutual funds Highest open interest Highest implied volatility Currency converter Sectors Basic materials Communication services Consumer cyclical Co

### Ćwiczenie 3: Napisz program do pobrania tekstu ze strony Wydziału Matematyki i Informatyki. Pobierz cały tekst ze strony głównej a następnie wyszukaj na tej stronie wszystkich linków wewnętrznych i pobierz tekst ze stron wskazywanych przez te linki. Nie zagłębiaj się już dalej.


In [30]:
def scrape_text(soup):
    # Delete script and style elements
    for script in soup(["script", "style"]):
        script.extract()

    # Get text
    text = soup.get_text()
    
    return text

def scrape_wmi():
    url = "https://wmi.amu.edu.pl/"

    page = requests.get(url)
    soup = BeautifulSoup(page.content, 'html.parser')

    # Create list to store text elements
    text_elements = []

    text = scrape_text(soup)
    text_elements.append(text)

    # Find all links
    links = soup.find_all('a')

    # Get href from links
    links = [link.get('href') for link in links]

    # Get text from links
    for link in links:
        try:
            page = requests.get(link)
            soup = BeautifulSoup(page.content, 'html.parser')
            text = scrape_text(soup)
            text_elements.append(text)
        except:
            pass
    
    return text_elements

In [31]:
len(scrape_wmi())

109

Omówione wyżej techniki działają również bardzo dobrze dla zasobów słownikowych.

### Ćwiczenie 4: Pobierz jak najwięcej słów w języku albańskim z serwisu glosbe.com.

Rozumiem, że w tym zadaniu nie można skorzystać z biblioteki zawierającej np słownik z polskimi wyrazami (zbyt trywialne) - dlatego skorzystam ze słów z poprzedniego zadania, użyje lematyzacji i przetłumaczę je za pomocą serwisu

In [44]:
import spacy

def scrape_shqip(limit: int = 10):
    base_url = "https://glosbe.com/pl/sq/"
    unique_polish_words = list(set(" ".join(scrape_wmi()).split()))
    unique_polish_words = [word.lower() for word in unique_polish_words if word.isalpha()]
    unique_polish_words = unique_polish_words[:limit]

    print(f"Polish words to translate: {unique_polish_words}", end="\n\n\n")

    nlp = spacy.load("pl_core_news_sm")
    doc = nlp(" ".join(unique_polish_words))

    albanian_translations = {}
    for word in doc:
        word = word.lemma_

        url = f"{base_url}{word}"
        page = requests.get(url)
        soup = BeautifulSoup(page.content, 'html.parser')

        try:
            albanian_word = soup.find('li', {'data-element':'translation'})
            albanian_word = albanian_word.find('h3')
            albanian_word = albanian_word.get_text().strip()

            print(f"{word} -> {albanian_word}")
            albanian_translations[word] = albanian_word
        except:
            print(f"{word} -> None")
            albanian_translations[word] = None

    return albanian_translations

In [45]:
albanian_translations = scrape_shqip(limit=50)

Polish words to translate: ['samorządu', 'ilorazowe', 'dużym', 'filozofii', 'zmienione', 'załączonych', 'wynikami', 'kampusie', 'powołać', 'matematycznego', 'uz', 'ostatniej', 'stopień', 'podręczników', 'advancedbeststudentgrant', 'filmy', 'powodu', 'infrastruktura', 'sesja', 'javascritp', 'wykładowcę', 'koordynatorką', 'minimalnych', 'administracyjnych', 'symulowania', 'soil', 'indeks', 'mail', 'konfigurujemy', 'skutki', 'analizując', 'humboldt', 'zainteresowane', 'trzyletnich', 'otwartością', 'mający', 'doradczyzielony', 'ustalonej', 'przykładów', 'czajkowskiizabela', 'sławomir', 'różniczkowychseminarium', 'przygotowuje', 'zdobywali', 'wjazd', 'wspinaczkowych', 'usługę', 'danychna', 'zastępowane', 'rozproszonym']


samorząd -> None
ilorazowy -> None
duży -> madh
filozofia -> filozofia
zmienić -> ndryshoj
załączony -> None
wynik -> rezultat
kampus -> None
powołać -> None
matematyczny -> None
uz -> None
ostatni -> vonë
stopień -> gradë
podręcznik -> libër shkollor
advancedbeststudentgr